In [11]:
import ffn
import numpy as np
import pandas as pd
import plotly as py
import plotly.graph_objs as go

In [12]:
from plotly.offline import init_notebook_mode, iplot
init_notebook_mode()

In [13]:
def get_ticker_yahoo(ticker, data_frame, name=None):
    vals = ffn.get(ticker, start=data_frame['date'][0])
    ticker_vals = []
    for date in data_frame['date'].tolist():
        try:
            ticker_vals.append(float(vals.loc[str(date)]))
        except KeyError:
            ticker_vals.append(None)
    if name is None:
        data_frame[ticker] = ticker_vals
    else:
        data_frame[name] = ticker_vals
    return data_frame

In [14]:
bonds_daily = pd.read_csv('Data/Bond_Yeilds_Daily.csv', skiprows=[0,1,2,3,4,5], skipinitialspace=True)
bonds_daily = bonds_daily.replace('ND', np.nan)
# bonds_daily = bonds_daily.set_index('date')

In [15]:
bonds_daily

date m3 yield m6 yield y1 yield y5 yield y5 inflation indexed  \
0      1982-01-01      NaN      NaN      NaN      NaN                  NaN   
1      1982-01-04    11.87    13.16    13.56    14.15                  NaN   
2      1982-01-05    12.20    13.41    13.83    14.41                  NaN   
3      1982-01-06    12.16    13.46    13.91    14.60                  NaN   
4      1982-01-07    12.17    13.43    13.93    14.66                  NaN   
...           ...      ...      ...      ...      ...                  ...   
10220  2021-03-05     0.04     0.07     0.08     0.79                -1.64   
10221  2021-03-08     0.05     0.06     0.09     0.86                -1.56   
10222  2021-03-09     0.05     0.07     0.10     0.83                -1.58   
10223  2021-03-10     0.04     0.06     0.08     0.80                -1.67   
10224  2021-03-11     0.04     0.05     0.08     0.78                -1.73   

      y10 yield y10 inflation indexed m3 secondary m6 secondary y1 secondary  
0           NaN                   NaN          NaN          NaN          NaN  
1         14.19                   NaN        11.39        12.20        12.15  
2         14.44                   NaN        11.72        12.42        12.37  
3         14.59                   NaN        11.64        12.44        12.43  
4         14.63                   NaN        11.66        12.46        12.45  
...         ...                   ...          ...          ...          ...  
10220      1.56                 -0.66         0.04         0.07         0.08  
10221      1.59                 -0.62         0.05         0.06         0.09  
10222      1.55                 -0.66         0.05         0.07         0.10  
10223      1.53                 -0.73         0.04         0.06         0.08  
10224      1.54                 -0.74         0.04         0.05         0.08  

[10225 rows x 11 columns]

In [16]:
bond_plus = get_ticker_yahoo('spy', bonds_daily)

In [17]:
# 2003-12-01 is oldest price date from yahoo -> need another source
# Besides 1 year secondary market, this is our limiting factor for now
bond_plus = get_ticker_yahoo('EURUSD=X', bonds_daily, name='eur_usd')

In [18]:
bond = bond_plus.set_index('date')
bond = bond['2003-12-01':]
bond = bond.drop(columns=['y1 secondary'])
bond

m3 yield m6 yield y1 yield y5 yield y5 inflation indexed y10 yield  \
date                                                                            
2003-12-01     0.95     1.06     1.41     3.46                 1.42      4.40   
2003-12-02     0.94     1.04     1.38     3.43                 1.38      4.38   
2003-12-03     0.94     1.04     1.39     3.46                 1.40      4.41   
2003-12-04     0.93     1.04     1.38     3.42                 1.35      4.38   
2003-12-05     0.92     1.01     1.30     3.23                 1.20      4.23   
...             ...      ...      ...      ...                  ...       ...   
2021-03-05     0.04     0.07     0.08     0.79                -1.64      1.56   
2021-03-08     0.05     0.06     0.09     0.86                -1.56      1.59   
2021-03-09     0.05     0.07     0.10     0.83                -1.58      1.55   
2021-03-10     0.04     0.06     0.08     0.80                -1.67      1.53   
2021-03-11     0.04     0.05     0.08     0.78                -1.73      1.54   

           y10 inflation indexed m3 secondary m6 secondary         spy  \
date                                                                     
2003-12-01                  2.08         0.93         1.04   76.113182   
2003-12-02                  2.05         0.92         1.02   75.922203   
2003-12-03                  2.08         0.92         1.02   75.801964   
2003-12-04                  2.04         0.91         1.02   76.113182   
2003-12-05                  1.92         0.90         0.99   75.582664   
...                          ...          ...          ...         ...   
2021-03-05                 -0.66         0.04         0.07  382.377625   
2021-03-08                 -0.62         0.05         0.06  380.473846   
2021-03-09                 -0.66         0.05         0.07  385.906067   
2021-03-10                 -0.73         0.04         0.06  388.308197   
2021-03-11                 -0.74         0.04         0.05  392.245300   

             eur_usd  
date                  
2003-12-01  1.196501  
2003-12-02  1.208897  
2003-12-03  1.212298  
2003-12-04  1.208094  
2003-12-05  1.218695  
...              ...  
2021-03-05  1.196774  
2021-03-08  1.192563  
2021-03-09  1.185171  
2021-03-10  1.189791  
2021-03-11  1.192606  

[4509 rows x 11 columns]

In [9]:
# bond[bond['spy'] == bond['spy'].shift(periods=-1)]

In [10]:
bond['m3 yield'] = pd.to_numeric(bond['m3 yield'], errors='coerce')
bond['m6 yield'] = pd.to_numeric(bond['m6 yield'], errors='coerce')
bond['y1 yield'] = pd.to_numeric(bond['y1 yield'], errors='coerce')
bond['y5 yield'] = pd.to_numeric(bond['y5 yield'], errors='coerce')
bond['y5 inflation indexed'] = pd.to_numeric(bond['y5 inflation indexed'], errors='coerce')
bond['y10 yield'] = pd.to_numeric(bond['y10 yield'], errors='coerce')
bond['y10 inflation indexed'] = pd.to_numeric(bond['y10 inflation indexed'], errors='coerce')
bond['m3 secondary'] = pd.to_numeric(bond['m3 secondary'], errors='coerce')
bond['m6 secondary'] = pd.to_numeric(bond['m6 secondary'], errors='coerce')

In [11]:
bond['inverse spy'] = bond['spy'] * -1

In [12]:
corr = bond.corr()
corr

m3 yield  m6 yield  y1 yield  y5 yield  \
m3 yield               1.000000  0.997728  0.992098  0.871487   
m6 yield               0.997728  1.000000  0.997618  0.887519   
y1 yield               0.992098  0.997618  1.000000  0.907811   
y5 yield               0.871487  0.887519  0.907811  1.000000   
y5 inflation indexed   0.759928  0.782536  0.805204  0.899954   
y10 yield              0.703925  0.722858  0.747361  0.943336   
y10 inflation indexed  0.655132  0.679589  0.707182  0.898563   
m3 secondary           0.999989  0.997838  0.992335  0.871814   
m6 secondary           0.997506  0.999973  0.997835  0.887928   
spy                   -0.153728 -0.174275 -0.194364 -0.447224   
eur_usd                0.020155  0.022862  0.020801  0.201198   
inverse spy            0.153728  0.174275  0.194364  0.447224   

                       y5 inflation indexed  y10 yield  y10 inflation indexed  \
m3 yield                           0.759928   0.703925               0.655132   
m6 yield                           0.782536   0.722858               0.679589   
y1 yield                           0.805204   0.747361               0.707182   
y5 yield                           0.899954   0.943336               0.898563   
y5 inflation indexed               1.000000   0.840270               0.947836   
y10 yield                          0.840270   1.000000               0.934642   
y10 inflation indexed              0.947836   0.934642               1.000000   
m3 secondary                       0.760047   0.704024               0.655184   
m6 secondary                       0.782895   0.722899               0.679769   
spy                               -0.425604  -0.663530              -0.627119   
eur_usd                            0.119112   0.423873               0.325784   
inverse spy                        0.425604   0.663530               0.627119   

                       m3 secondary  m6 secondary       spy   eur_usd  \
m3 yield                   0.999989      0.997506 -0.153728  0.020155   
m6 yield                   0.997838      0.999973 -0.174275  0.022862   
y1 yield                   0.992335      0.997835 -0.194364  0.020801   
y5 yield                   0.871814      0.887928 -0.447224  0.201198   
y5 inflation indexed       0.760047      0.782895 -0.425604  0.119112   
y10 yield                  0.704024      0.722899 -0.663530  0.423873   
y10 inflation indexed      0.655184      0.679769 -0.627119  0.325784   
m3 secondary               1.000000      0.997643 -0.153073  0.019391   
m6 secondary               0.997643      1.000000 -0.172810  0.021498   
spy                       -0.153073     -0.172810  1.000000 -0.608457   
eur_usd                    0.019391      0.021498 -0.608457  1.000000   
inverse spy                0.153073      0.172810 -1.000000  0.608457   

                       inverse spy  
m3 yield                  0.153728  
m6 yield                  0.174275  
y1 yield                  0.194364  
y5 yield                  0.447224  
y5 inflation indexed      0.425604  
y10 yield                 0.663530  
y10 inflation indexed     0.627119  
m3 secondary              0.153073  
m6 secondary              0.172810  
spy                      -1.000000  
eur_usd                   0.608457  
inverse spy               1.000000

In [13]:
trace = go.Heatmap(
    x = bond.columns,
    y = bond.columns,
    z = corr.values,
    type = 'heatmap',
    colorscale = 'icefire',
    showscale=True
)
data = [trace]
fig = go.Figure(data=data)
fig.show()
# iplot(fig)

In [15]:
all_vals = bond.dropna()

model = np.polyfit(all_vals['spy'], all_vals['eur_usd'], 2)
fit = np.poly1d(model)

out = fit(bond['spy'])

fig = go.Figure()
fig.add_trace(go.Scatter(
        x=bond['spy'],
        y=bond['eur_usd'],
        mode='markers',
        name='spy to eur'))
fig.add_trace(go.Scatter(
        x=bond['spy'],
        y=out,
        mode='lines',
        name='model'))
fig.show()

In [16]:
from plotly.subplots import make_subplots
fig = make_subplots(specs=[[{"secondary_y": True}]])
fig.add_trace(go.Scatter(
        x=bond.index,
        y=bond['spy'],
        mode='lines',
        name='SPY'))
fig.add_trace(go.Scatter(
        x=bond.index,
        y=bond['eur_usd'],
        mode='lines',
        name='Eur/USD'), 
             secondary_y=True)
fig.show()

In [17]:
bond_targeted = bond[['m6 yield', 'y5 yield', 'y10 yield','spy', 'eur_usd']]

import plotly.express as px
fig = px.scatter_matrix(bond_targeted,
    dimensions=['m6 yield', 'y5 yield', 'y10 yield','spy', 'eur_usd'],
        #color=bond_targeted.index,
        #color_continuous_scale='viridis'
                       )
fig.show()

In [18]:
ffr = pd.read_csv('Data/FederalFundsWeekly.csv', skiprows=[0,1,2,3,4,5], skipinitialspace=True)
ffr = ffr.replace('ND', np.nan)
ffr['date'] = pd.to_datetime(ffr['date'], infer_datetime_format=False)

cpi = pd.read_csv('Data/cpi_roc_monthly.csv')
cpi = cpi[cpi['LOCATION']=='USA']
cpi['date'] = pd.to_datetime(cpi['TIME'], infer_datetime_format=False)
cpi = cpi[['date', 'Value']]
cpi = cpi.rename(columns={"Value":"CPI"})

gdp = pd.read_csv('Data/gdp_roc_quarterly.csv')
gdp = gdp[gdp['LOCATION']=='USA']
gdp['date'] = pd.to_datetime(gdp['TIME'], infer_datetime_format=False)
gdp = gdp[['date', 'Value']]
gdp = gdp.rename(columns={"Value":"GDP"})

In [19]:
bond_targeted = bond_targeted[['m6 yield', 'y5 yield', 'y10 yield','spy', 'eur_usd']]
bond_targeted.reset_index(inplace=True)
bond_targeted['date'] = pd.to_datetime(bond_targeted['date'])
bond_targeted

date  m6 yield  y5 yield  y10 yield         spy   eur_usd
0    2003-12-01      1.06      3.46       4.40   76.113182  1.196501
1    2003-12-02      1.04      3.43       4.38   75.922203  1.208897
2    2003-12-03      1.04      3.46       4.41   75.801964  1.212298
3    2003-12-04      1.04      3.42       4.38   76.113182  1.208094
4    2003-12-05      1.01      3.23       4.23   75.582664  1.218695
...         ...       ...       ...        ...         ...       ...
4504 2021-03-05      0.07      0.79       1.56  382.377625  1.196774
4505 2021-03-08      0.06      0.86       1.59  380.473846  1.192563
4506 2021-03-09      0.07      0.83       1.55  385.906067  1.185171
4507 2021-03-10      0.06      0.80       1.53  388.308197  1.189791
4508 2021-03-11      0.05      0.78       1.54  392.245300  1.192606

[4509 rows x 6 columns]

In [20]:
data = (pd.merge(bond_targeted, cpi, on='date', how='outer')
        .sort_values('date'))

data = (pd.merge(data, gdp, on='date', how='outer')
        .sort_values('date'))

data = (pd.merge(data, ffr, on='date', how='outer')
        .sort_values('date')
        .set_index('date'))

In [21]:
data = data.dropna(subset=['eur_usd'])
data = data.fillna(method='ffill')
data = data[data['GDP'].first_valid_index():]
data = data.drop(['AMPR', 'PCRA'], axis=1)
data

m6 yield  y5 yield  y10 yield         spy   eur_usd       CPI  \
date                                                                        
2004-01-01      1.02      3.25       4.27   79.088287  1.258194  1.926252   
2004-01-02      1.02      3.36       4.38   79.052704  1.258194  1.926252   
2004-01-05      1.05      3.39       4.41   79.912697  1.268698  1.926252   
2004-01-06      1.03      3.26       4.29   79.990868  1.272103  1.926252   
2004-01-07      1.02      3.25       4.27   80.260941  1.264095  1.926252   
...              ...       ...        ...         ...       ...       ...   
2021-03-05      0.07      0.79       1.56  382.377625  1.196774  1.399770   
2021-03-08      0.06      0.86       1.59  380.473846  1.192563  1.399770   
2021-03-09      0.07      0.83       1.55  385.906067  1.185171  1.399770   
2021-03-10      0.06      0.80       1.53  388.308197  1.189791  1.399770   
2021-03-11      0.05      0.78       1.54  392.245300  1.192606  1.399770   

                 GDP  FFER  
date                        
2004-01-01  0.533747  0.96  
2004-01-02  0.533747  0.96  
2004-01-05  0.533747  0.96  
2004-01-06  0.533747  0.96  
2004-01-07  0.533747  0.97  
...              ...   ...  
2021-03-05  1.007613  0.07  
2021-03-08  1.007613  0.07  
2021-03-09  1.007613  0.07  
2021-03-10  1.007613  0.07  
2021-03-11  1.007613  0.07  

[3926 rows x 8 columns]

In [22]:
data['y'] = data['eur_usd'].shift(periods=-1)
data['class'] = data['eur_usd'].shift(periods=-1)
data.drop(data.tail(1).index,inplace=True)
data['dir'] = np.sign(data['y'] - data['eur_usd'])
max_eur = data['class'].max()
min_eur = data['class'].min()
rng = data['class'].max() - data['class'].min()
data['class'] = pd.cut(data['class'], 
              bins=[0, (min_eur + rng * .1), (min_eur + rng * .2), (min_eur + rng * .3), (min_eur + rng * .4), (min_eur + rng * .5), (min_eur + rng * .6), (min_eur + rng * .7), (min_eur + rng * .8), (min_eur + rng * .9), max_eur], 
              labels=[0, 10, 20, 30, 40, 50, 60, 70, 80, 90])
#data = data[data['dir'] != 0]
# data['dir'] = data['dir'].astype('category')
data

m6 yield  y5 yield  y10 yield         spy   eur_usd       CPI  \
date                                                                        
2004-01-01      1.02      3.25       4.27   79.088287  1.258194  1.926252   
2004-01-02      1.02      3.36       4.38   79.052704  1.258194  1.926252   
2004-01-05      1.05      3.39       4.41   79.912697  1.268698  1.926252   
2004-01-06      1.03      3.26       4.29   79.990868  1.272103  1.926252   
2004-01-07      1.02      3.25       4.27   80.260941  1.264095  1.926252   
...              ...       ...        ...         ...       ...       ...   
2021-03-04      0.07      0.77       1.54  375.470245  1.205066  1.399770   
2021-03-05      0.07      0.79       1.56  382.377625  1.196774  1.399770   
2021-03-08      0.06      0.86       1.59  380.473846  1.192563  1.399770   
2021-03-09      0.07      0.83       1.55  385.906067  1.185171  1.399770   
2021-03-10      0.06      0.80       1.53  388.308197  1.189791  1.399770   

                 GDP  FFER         y class  dir  
date                                             
2004-01-01  0.533747  0.96  1.258194    30  0.0  
2004-01-02  0.533747  0.96  1.268698    40  1.0  
2004-01-05  0.533747  0.96  1.272103    40  1.0  
2004-01-06  0.533747  0.96  1.264095    40 -1.0  
2004-01-07  0.533747  0.97  1.277498    40  1.0  
...              ...   ...       ...   ...  ...  
2021-03-04  1.007613  0.07  1.196774    20 -1.0  
2021-03-05  1.007613  0.07  1.192563    20 -1.0  
2021-03-08  1.007613  0.07  1.185171    20 -1.0  
2021-03-09  1.007613  0.07  1.189791    20  1.0  
2021-03-10  1.007613  0.07  1.192606    20  1.0  

[3925 rows x 11 columns]

In [26]:
data.to_csv('Data/us_daily_data.csv')

In [23]:
from sklearn.decomposition import PCA
features = ["m6 yield", "y5 yield", "y10 yield", "spy", "eur_usd", "CPI", "FFER"]

pca = PCA()
components = pca.fit_transform(data[features])
labels = {
    str(i): f"{var:.1f}%"
    for i, var in enumerate(pca.explained_variance_ratio_ * 100)
}
fig = px.scatter_matrix(
    components,
    labels=labels,
    dimensions=range(len(features)),
    color=data["class"]
)
fig.update_traces(diagonal_visible=False)
fig.show()

In [24]:
fig = px.scatter_matrix(data,
    dimensions=features,
        #color=bond_targeted.index,
        #color_continuous_scale='viridis'
                       )
fig.update_traces(diagonal_visible=False)
fig.show()

In [25]:
from statsmodels.tsa.stattools import grangercausalitytests
max_lags = 8
for i, feature in enumerate(features):
    results=grangercausalitytests(data[['y',feature]], max_lags, verbose=False)
    p_values=[round(results[i+1][0]['ssr_ftest'][1],4) for i in range(max_lags)]
    print('Column - {} : P_Values - {}'.format(feature,p_values))

Column - m6 yield : P_Values - [0.3754, 0.0307, 0.0568, 0.0013, 0.003, 0.006, 0.0079, 0.01]
Column - y5 yield : P_Values - [0.3884, 0.0436, 0.069, 0.1122, 0.0007, 0.0013, 0.0019, 0.0023]
Column - y10 yield : P_Values - [0.1495, 0.0833, 0.15, 0.2314, 0.0013, 0.0029, 0.0058, 0.0065]
Column - spy : P_Values - [0.0427, 0.1988, 0.2631, 0.2313, 0.0313, 0.0412, 0.059, 0.106]
Column - eur_usd : P_Values - [0.0, 0.0013, 0.8509, 1.0, 0.9973, 0.9772, 0.1381, 0.9993]
Column - CPI : P_Values - [0.3353, 0.0072, 0.001, 0.0001, 0.0, 0.0, 0.0, 0.0]
Column - FFER : P_Values - [0.2529, 0.2333, 0.221, 0.3201, 0.2113, 0.2966, 0.0, 0.0]
